In [1]:
import os, glob, re, pickle
from functools import partial
from collections import OrderedDict
import operator as op
from cytoolz import compose

import pyscenic
import pandas as pd
import seaborn as sns
import numpy as np
import scanpy as sc
import anndata as ad
import matplotlib as mpl
import matplotlib.pyplot as plt
#from pyscenic.export import export2loom, add_scenic_metadata
from pyscenic.utils import load_motifs
from pyscenic.transform import df2regulons
from pyscenic.aucell import aucell
from pyscenic.binarization import binarize
from pyscenic.rss import regulon_specificity_scores
from pyscenic.plotting import plot_binarization, plot_rss

from IPython.display import HTML, display

In [2]:
# Set maximum number of jobs for Scanpy.
sc.settings.njobs = 96

Folder structure.

In [3]:
RESOURCES_FOLDERNAME = "/media/ggj/ggjlab/RData/agingatlas/MCA2/all/SCENIC/resources/"
AUXILLIARIES_FOLDERNAME = "/media/ggj/ggjlab/pySCENIC_use/"
RESULTS_FOLDERNAME = "/media/ggj/ggjlab/RData/agingatlas/MCA2/all/SCENIC/results/"
FIGURES_FOLDERNAME = "/media/ggj/ggjlab/RData/agingatlas/MCA2/all/SCENIC/results/figures/"

In [4]:
sc.settings.figdir = FIGURES_FOLDERNAME

Auxilliary functions.

In [5]:
BASE_URL = "http://motifcollections.aertslab.org/v9/logos/"
COLUMN_NAME_LOGO = "MotifLogo"
COLUMN_NAME_MOTIF_ID = "MotifID"
COLUMN_NAME_TARGETS = "TargetGenes"

In [6]:
def savesvg(fname: str, fig, folder: str=FIGURES_FOLDERNAME) -> None:
    """
    Save figure as vector-based SVG image format.
    """
    fig.tight_layout()
    fig.savefig(os.path.join(folder, fname), format='svg')

In [7]:
def display_logos(df: pd.DataFrame, top_target_genes: int = 3, base_url: str = BASE_URL):
    """
    :param df:
    :param base_url:
    """
    # Make sure the original dataframe is not altered.
    df = df.copy()
    
    # Add column with URLs to sequence logo.
    def create_url(motif_id):
        return '<img src="{}{}.png" style="max-height:124px;"></img>'.format(base_url, motif_id)
    df[("Enrichment", COLUMN_NAME_LOGO)] = list(map(create_url, df.index.get_level_values(COLUMN_NAME_MOTIF_ID)))
    
    # Truncate TargetGenes.
    def truncate(col_val):
        return sorted(col_val, key=op.itemgetter(1))[:top_target_genes]
    df[("Enrichment", COLUMN_NAME_TARGETS)] = list(map(truncate, df[("Enrichment", COLUMN_NAME_TARGETS)]))
    
    MAX_COL_WIDTH = pd.get_option('display.max_colwidth')
    pd.set_option('display.max_colwidth', -1)
    display(HTML(df.head().to_html(escape=False)))
    pd.set_option('display.max_colwidth', MAX_COL_WIDTH)

Auxilliary data sets.

In [8]:
# Downloaded fromm pySCENIC github repo: https://github.com/aertslab/pySCENIC/tree/master/resources
DMEL_TFS_FNAME = os.path.join(AUXILLIARIES_FOLDERNAME, 'mm_total_tfs.txt')
# Ranking databases. Downloaded from cisTargetDB: https://resources.aertslab.org/cistarget/
RANKING_DBS_FNAMES = list(map(lambda fn: os.path.join(AUXILLIARIES_FOLDERNAME, fn),
                       ['mm9-tss-centered-10kb-7species.mc9nr.feather',
                       'mm9-500bp-upstream-7species.mc9nr.feather',
                       'mm9-tss-centered-5kb-10species.mc9nr.feather']))
# Motif annotations. Downloaded from cisTargetDB: https://resources.aertslab.org/cistarget/
MOTIF_ANNOTATIONS_FNAME = os.path.join(AUXILLIARIES_FOLDERNAME, 'motifs-v9-nr.mgi-m0.001-o0.0.tbl')

In [9]:
DATASET_ID = "MCA2"
#TCGA_CODE = 'SKCM'

Resources downloaded.

In [10]:
# Downloaded from GEO on 28 FEB 2019.
CELL_ANNOTATIONS_FNAME = os.path.join(RESOURCES_FOLDERNAME, "all_tissue_stage_pseudocell100_anno.csv")
# Downloaded from Cell Journal website on 1 MAR 2019.
#SAMPLE_METADATA_FNAME = os.path.join(RESOURCES_FOLDERNAME, "1-s2.0-S0092867418311784-mmc1.xlsx")
# Downloaded from GEO on 1 MAR 2019.
EXP_MTX_TPM_FNAME = os.path.join(RESOURCES_FOLDERNAME, 'all_tissue_stage_pseudocell100.csv')
#EXP_MTX_COUNTS_FNAME = os.path.join(RESOURCES_FOLDERNAME, 'GSE115978_counts.csv')

Results created.

In [11]:
METADATA_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.metadata.csv'.format(DATASET_ID))
EXP_MTX_QC_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.qc.tpm.csv'.format(DATASET_ID))
ADJACENCIES_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.adjacencies.tsv'.format(DATASET_ID))
MOTIFS_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.motifs.csv'.format(DATASET_ID))
REGULONS_DAT_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.regulons.dat'.format(DATASET_ID))
AUCELL_MTX_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.auc_all.csv'.format(DATASET_ID))
BIN_MTX_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.bin.csv'.format(DATASET_ID))
THR_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.thresholds.csv'.format(DATASET_ID))
ANNDATA_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.h5ad'.format(DATASET_ID))
LOOM_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.loom'.format(DATASET_ID))

### STEP 0: Preprocessing

__METADATA CLEANING__

In [12]:
df_annotations = pd.read_csv(CELL_ANNOTATIONS_FNAME,index_col=0)
df_annotations

ctanno        cellID
cluster0.0     cluster0    cluster0.0
cluster0.1     cluster0    cluster0.1
cluster0.10    cluster0   cluster0.10
cluster0.100   cluster0  cluster0.100
cluster0.101   cluster0  cluster0.101
...                 ...           ...
cluster99.5   cluster99   cluster99.5
cluster99.6   cluster99   cluster99.6
cluster99.7   cluster99   cluster99.7
cluster99.8   cluster99   cluster99.8
cluster99.9   cluster99   cluster99.9

[11366 rows x 2 columns]

In [13]:
#df_annotations['samples'] = df_annotations['samples'].str.upper()
#df_annotations.rename(columns={'cell.types': 'cell_type', 'cells': 'cell_id', 'samples': 'sample_id', 
#                               'treatment.group': 'treatment_group', 'Cohort': 'cohort'}, inplace=True)
#df_annotations['cell_type'] = df_annotations.cell_type.replace({
#    'Mal': 'Malignant Cell',
#    'Endo.': 'Endothelial Cell',
#    'T.CD4': 'Thelper Cell',
#    'CAF': 'Fibroblast',
#    'T.CD8': 'Tcytotoxic Cell',
#    'T.cell': 'T Cell',
#    'NK': 'NK Cell',
#    'B.cell': 'B Cell'})
#df_samples = pd.read_excel(SAMPLE_METADATA_FNAME, header=2)
#df_samples = df_samples.drop(['Cohort'], axis=1)
#df_samples['Sample'] = df_samples.Sample.str.upper()
#df_metadata = pd.merge(df_annotations, df_samples, left_on='sample_id', right_on='Sample')
#df_metadata = df_metadata.drop(['Sample', 'treatment_group'], axis=1)
#df_metadata.rename(columns={'Patient': 'patient_id',
#                           'Age': 'age', 'Sex': 'sex', 'Lesion type': 'lesion_type', 'Site': 'site',
#                           'Treatment': 'treatment', 'Treatment group': 'treatment_group'}, inplace=True)

df_metadata = df_annotations
df_metadata.to_csv(METADATA_FNAME, index=False)
df_metadata.head()

ctanno        cellID
cluster0.0    cluster0    cluster0.0
cluster0.1    cluster0    cluster0.1
cluster0.10   cluster0   cluster0.10
cluster0.100  cluster0  cluster0.100
cluster0.101  cluster0  cluster0.101

__EXPRESSION MATRIX QC__

In [14]:
df_tpm = pd.read_csv(EXP_MTX_TPM_FNAME, index_col=0)
df_tpm

cluster99.0  cluster99.1  cluster99.10  cluster99.11  \
00R-AC107638.2     0.000000     0.000000      0.000000      0.000000   
0610005C13Rik     82.039534    95.142848     57.111139    135.184232   
0610006L08Rik      0.000000     0.000000      0.000000      0.000000   
0610007P14Rik     48.649653    37.910259     25.415542     28.918891   
0610009B22Rik     58.446606    38.641460     42.476447     77.281839   
...                     ...          ...           ...           ...   
Zyg11a             0.000000     0.000000      0.000000      0.000000   
Zyg11b            23.763310    10.908980     25.229010     20.583870   
Zyx               56.428150    65.148710     77.065030     38.727600   
Zzef1            135.078800   129.521700    151.530100    209.281500   
Zzz3              24.659040     7.514672     18.340210     25.339770   

                cluster99.12  cluster99.13  cluster99.14  cluster99.15  \
00R-AC107638.2       0.00000      0.000000      0.000000      0.000000   
0610005C13Rik      102.37744    100.003736     56.896348    116.342172   
0610006L08Rik        0.00000      0.000000      0.000000      0.000000   
0610007P14Rik       28.67165     74.305445     51.877824     37.317855   
0610009B22Rik       57.30205     65.871811     65.389136     20.307101   
...                      ...           ...           ...           ...   
Zyg11a               0.00000      0.000000      0.000000      0.000000   
Zyg11b              32.54795     31.608510     31.544720     24.961650   
Zyx                139.69620     99.601000     73.283480     71.335430   
Zzef1              191.83170    178.533000    293.598100    193.260200   
Zzz3                 0.00000     51.930330      0.000000     24.276700   

                cluster99.16  cluster99.17  ...  cluster0.90  cluster0.91  \
00R-AC107638.2      0.000000      0.000000  ...     0.000000     0.000000   
0610005C13Rik     158.408164    134.415266  ...     0.000000     0.000000   
0610006L08Rik       0.000000      0.000000  ...     0.000000     0.000000   
0610007P14Rik      63.907307     90.318160  ...    52.713212    52.344224   
0610009B22Rik      36.689738     91.811500  ...   140.404973   125.613183   
...                      ...           ...  ...          ...          ...   
Zyg11a              0.000000      0.000000  ...     0.000000     0.000000   
Zyg11b             37.784210     60.342720  ...    18.050540    38.203910   
Zyx                37.591490     76.411840  ...   140.317900    91.396820   
Zzef1             264.214800    210.573800  ...    34.477440    18.115940   
Zzz3               10.438410     14.164310  ...     0.000000    17.241380   

                cluster0.92  cluster0.93  cluster0.94  cluster0.95  \
00R-AC107638.2     0.000000     0.000000     0.000000     0.000000   
0610005C13Rik      0.000000     0.000000     0.000000     0.000000   
0610006L08Rik      0.000000     0.000000     0.000000     0.000000   
0610007P14Rik    109.938467    57.756987     0.000000    83.820941   
0610009B22Rik    111.543453    94.965881   121.189855   124.747882   
...                     ...          ...          ...          ...   
Zyg11a             0.000000     0.000000     0.000000     0.000000   
Zyg11b             0.000000     0.000000     0.000000    59.532680   
Zyx              206.633500    73.346620    19.841270    40.486650   
Zzef1             37.843800     0.000000    18.975330     0.000000   
Zzz3              58.473310    17.636680     0.000000    62.373340   

                cluster0.96  cluster0.97  cluster0.98  cluster0.99  
00R-AC107638.2     0.000000     0.000000     0.000000     0.000000  
0610005C13Rik      0.000000     0.000000     0.000000     0.000000  
0610006L08Rik      0.000000     0.000000     0.000000     0.000000  
0610007P14Rik     82.576931    65.110319    71.437923    60.653023  
0610009B22Rik    126.737826    80.730978   109.135828    40.548435  
...                     ...          ...          ...          ...  
Zyg11a       

In [15]:
#df_counts = pd.read_csv(EXP_MTX_COUNTS_FNAME, index_col=0)
#df_counts.shape

In [15]:
adata = sc.AnnData(X=df_tpm.T.sort_index())
df_obs = df_metadata[['ctanno','cellID']].set_index('cellID').sort_index()
adata.obs = df_obs
adata.var_names_make_unique()
sc.pp.filter_cells(adata, min_genes=0)
sc.pp.filter_genes(adata, min_cells=3)
# Store non-log transformed data as raw. This data can be used via the use_raw parameters available for many functions.
# In the scanpy's tutorials this is used to stored all genes in log-transformed counts before retaining only Highly Variable Genes (HVG). 
# Because in this case no filtering is done we use this feature to store raw counts.
adata.raw = adata 
sc.pp.log1p(adata)
adata

AnnData object with n_obs × n_vars = 11366 × 29677
    obs: 'ctanno', 'n_genes'
    var: 'n_cells'
    uns: 'log1p'

In [16]:
adata.write_h5ad(ANNDATA_FNAME) # Categorical dtypes are created.

... storing 'ctanno' as categorical


In [17]:
adata.to_df().to_csv(EXP_MTX_QC_FNAME)

### STEP 1: Network inference based on GRNBoost2 from CLI

For this step the CLI version of SCENIC is used. This step can be deployed on an High Performance Computing system.

_Output:_ List of adjacencies between a TF and its targets stored in `ADJACENCIES_FNAME`.

need env:pyscenic

In [18]:
!pyscenic grn {EXP_MTX_QC_FNAME} {DMEL_TFS_FNAME} -o {ADJACENCIES_FNAME} --num_workers 36


2022-02-28 00:24:50,938 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.

2022-02-28 00:27:51,649 - pyscenic.cli.pyscenic - INFO - Inferring regulatory networks.
/home/ggj/anaconda3/lib/python3.8/site-packages/distributed/node.py:151: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 36239 instead
  warnings.warn(
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a no

In [12]:
import pyscenic
import dask
print(pyscenic.__version__)
print(dask.__version__)

0.10.3
1.0.0


```
2019-04-25 11:22:20,360 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.
2019-04-25 11:23:37,612 - pyscenic.cli.pyscenic - INFO - Inferring regulatory networks.
preparing dask client
parsing input
creating dask graph
4 partitions
computing dask graph
not shutting down client, client was created externally
finished
2019-04-26 03:58:01,096 - pyscenic.cli.pyscenic - INFO - Writing results to file.
```

### STEP 2-3: Regulon prediction aka cisTarget from CLI

For this step the CLI version of SCENIC is used. This step can be deployed on an High Performance Computing system.

_Output:_ List of adjacencies between a TF and its targets stored in `MOTIFS_FNAME`.

In [12]:
DBS_PARAM = ' '.join(RANKING_DBS_FNAMES)
DBS_PARAM

'/media/ggj/ggjlab/pySCENIC_use/mm9-tss-centered-10kb-7species.mc9nr.feather /media/ggj/ggjlab/pySCENIC_use/mm9-500bp-upstream-7species.mc9nr.feather /media/ggj/ggjlab/pySCENIC_use/mm9-tss-centered-5kb-10species.mc9nr.feather'

In [13]:
!pyscenic ctx {ADJACENCIES_FNAME} {DBS_PARAM} \
            --annotations_fname {MOTIF_ANNOTATIONS_FNAME} \
            --expression_mtx_fname {EXP_MTX_QC_FNAME} \
            --output {MOTIFS_FNAME} \
            --num_workers 4


2022-03-01 11:42:18,931 - pyscenic.cli.pyscenic - INFO - Creating modules.

2022-03-01 11:42:32,101 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.

2022-03-01 11:47:47,089 - pyscenic.utils - INFO - Calculating Pearson correlations.

2022-03-01 11:47:55,317 - pyscenic.utils - WARNING - Note on correlation calculation: the default behaviour for calculating the correlations has changed after pySCENIC verion 0.9.16. Previously, the default was to calculate the correlation between a TF and target gene using only cells with non-zero expression values (mask_dropouts=True). The current default is now to use all cells to match the behavior of the R verision of SCENIC. The original settings can be retained by setting 'rho_mask_dropouts=True' in the modules_from_adjacencies function, or '--mask_dropouts' from the CLI.
	Dropout masking is currently set to [False].

2022-03-01 11:58:34,321 - pyscenic.utils - INFO - Creating modules.

2022-03-01 12:10:32,078 - pyscenic.cli.pyscenic - I

[                                        ] | 0% Completed | 31.9s
2022-03-01 12:11:06,519 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for 5730507C01Rik could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 32.0s
2022-03-01 12:11:06,615 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for 9130019O22Rik could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 32.2s
2022-03-01 12:11:06,780 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for 9130023H24Rik could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 32.3s
2022-03-01 12:11:06,888 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for A430033K04Rik could be mapped to mm9-tss-centered-5kb-10speci

[                                        ] | 0% Completed | 36.7s
2022-03-01 12:11:11,337 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Gmeb1 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 36.8s
2022-03-01 12:11:11,357 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Aff2 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 37.0s
2022-03-01 12:11:11,559 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Gmeb2 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.

2022-03-01 12:11:11,579 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Aff3 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 37.3s
2

[                                        ] | 0% Completed | 54.0s
2022-03-01 12:11:28,561 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Arid3a could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 54.1s
2022-03-01 12:11:28,659 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Esx1 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 54.2s
2022-03-01 12:11:28,758 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Arid3b could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 54.3s
2022-03-01 12:11:28,856 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Arid3c could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module

[                                        ] | 0% Completed |  1min 30.2s
2022-03-01 12:12:04,707 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Barhl1 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed |  1min 32.7s
2022-03-01 12:12:07,303 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Barhl2 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed |  1min 33.5s
2022-03-01 12:12:08,068 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Barx1 could be mapped to mm9-tss-centered-5kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed |  1min 33.9s
2022-03-01 12:12:08,446 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Fli1 could be mapped to mm9-tss-centered-5kb-10species.mc9n

...


2022-03-01 14:29:42,796 - pyscenic.transform - WARNING - Less than 80% of the genes in Zfp418 could be mapped to mm9-500bp-upstream-7species.mc9nr. Skipping this module.
[####################################### ] | 97% Completed |  2hr 19min  8.4s
2022-03-01 14:29:42,997 - pyscenic.transform - WARNING - Less than 80% of the genes in Zfp42 could be mapped to mm9-500bp-upstream-7species.mc9nr. Skipping this module.
[####################################### ] | 97% Completed |  2hr 19min  8.6s
2022-03-01 14:29:43,178 - pyscenic.transform - WARNING - Less than 80% of the genes in Zfp422 could be mapped to mm9-500bp-upstream-7species.mc9nr. Skipping this module.
[####################################### ] | 97% Completed |  2hr 19min  8.8s
2022-03-01 14:29:43,349 - pyscenic.transform - WARNING - Less than 80% of the genes in Zfp423 could be mapped to mm9-500bp-upstream-7species.mc9nr. Skipping this module.
[####################################### ] | 97% Completed |  2hr 19min  8.9s
2022-03-

[####################################### ] | 97% Completed |  2hr 19min 27.2s
2022-03-01 14:30:01,726 - pyscenic.transform - WARNING - Less than 80% of the genes in Hmx2 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 19min 29.5s
2022-03-01 14:30:03,989 - pyscenic.transform - WARNING - Less than 80% of the genes in Hmx3 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 19min 31.2s
2022-03-01 14:30:05,780 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Tbx21 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 19min 31.4s
2022-03-01 14:30:05,907 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Tbx22 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. 

[####################################### ] | 98% Completed |  2hr 20min  8.7s
2022-03-01 14:30:43,181 - pyscenic.transform - WARNING - Less than 80% of the genes in Hoxa3 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 20min 10.4s
2022-03-01 14:30:44,895 - pyscenic.transform - WARNING - Less than 80% of the genes in Hoxa4 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 20min 13.5s
2022-03-01 14:30:48,054 - pyscenic.transform - WARNING - Less than 80% of the genes in Hoxa7 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 20min 16.2s
2022-03-01 14:30:50,727 - pyscenic.transform - WARNING - Less than 80% of the genes in Hoxa9 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.


[####################################### ] | 98% Completed |  2hr 22min  9.9s
2022-03-01 14:32:44,502 - pyscenic.transform - WARNING - Less than 80% of the genes in Ikzf2 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 22min 10.8s
2022-03-01 14:32:45,357 - pyscenic.transform - WARNING - Less than 80% of the genes in Ikzf3 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 22min 10.9s
2022-03-01 14:32:45,476 - pyscenic.transform - WARNING - Less than 80% of the genes in Ikzf4 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed |  2hr 22min 11.1s
2022-03-01 14:32:45,668 - pyscenic.transform - WARNING - Less than 80% of the genes in Ikzf5 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.


[####################################### ] | 99% Completed |  2hr 24min 17.0s
2022-03-01 14:34:51,514 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Otp could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 99% Completed |  2hr 24min 17.1s
2022-03-01 14:34:51,638 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Otx1 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 99% Completed |  2hr 24min 17.4s
2022-03-01 14:34:52,000 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Otx2 could be mapped to mm9-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################### ] | 99% Completed |  2hr 24min 20.1s
2022-03-01 14:34:54,701 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Ovol2 could be mapped to mm9-tss-centered

```
2019-04-26 10:23:50,395 - pyscenic.cli.pyscenic - INFO - Creating modules.
2019-04-26 10:23:56,229 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.
2019-04-26 10:29:09,101 - pyscenic.cli.pyscenic - INFO - Loading databases.
2019-04-26 10:29:09,101 - pyscenic.cli.pyscenic - INFO - Calculating regulons.
2019-04-26 11:11:10,784 - pyscenic.cli.pyscenic - INFO - Writing results to file
```

The results is a list of enriched motifs for the modules.

| Column name | Description |
| ----------- | ----------- |
| TF | Transcription Factor (TF) for which an enriched motif is discovered. |
| motifID | The identifier of the enriched motif. |
| AUC | Area Under the recovery Curve statistic for this enriched motif. |
| NES | Normalized Enrichment Score for this enriched motif. |
| Context | Collection of tags clarifying the origin of the module for this factor: e.g. ranking database, ... |
| Annotation | Verbose description of the annotation available for this motif. |
| MotifSimilarityQvalue | The TomTom derived Q-value for motif similarity (if used for assigning the factor to this enriched motif). |
| OrthologousIdentity | The Amino Acid Identity between factors (if used for assigning the factor to this enriched motif). |
| RankAtMax | The position of the Leading Edge which is used as a threshold on the whole genome ranking of the motif to decide if a gene in the input is a direct target of a TF that binds this motif. |
| TargetGenes | A list of pairs: genes and their associated weights from GENIE3/GRNBoost2. |

In [14]:
df_motifs = load_motifs(MOTIFS_FNAME)

In [15]:
df_motifs.head()

Enrichment            \
                                                 AUC       NES   
TF    MotifID                                                    
Arnt2 swissregulon__hs__AHR_ARNT_ARNT2.p2   0.053641  3.131379   
Atf3  transfac_pro__M08931                  0.045328  3.734176   
      dbcorrdb__JUN__ENCSR000EGH_1__m1      0.043691  3.274092   
      dbcorrdb__BCL3__ENCSR000BQH_1__m2     0.044044  3.373248   
      cisbp__M5050                          0.045232  3.707019   

                                                                 \
                                          MotifSimilarityQvalue   
TF    MotifID                                                     
Arnt2 swissregulon__hs__AHR_ARNT_ARNT2.p2              0.000000   
Atf3  transfac_pro__M08931                             0.000226   
      dbcorrdb__JUN__ENCSR000EGH_1__m1                 0.000773   
      dbcorrdb__BCL3__ENCSR000BQH_1__m2                0.000006   
      cisbp__M5050                                     0.000608   

                                                               \
                                          OrthologousIdentity   
TF    MotifID                                                   
Arnt2 swissregulon__hs__AHR_ARNT_ARNT2.p2            0.977528   
Atf3  transfac_pro__M08931                           1.000000   
      dbcorrdb__JUN__ENCSR000EGH_1__m1               1.000000   
      dbcorrdb__BCL3__ENCSR000BQH_1__m2              1.000000   
      cisbp__M5050                                   1.000000   

                                                                                              \
                                                                                  Annotation   
TF    MotifID                                                                                  
Arnt2 swissregulon__hs__AHR_ARNT_ARNT2.p2  gene is orthologous to ENSG00000172379 in H. s...   
Atf3  transfac_pro__M08931                 gene is annotated for similar motif hocomoco__...   
      dbcorrdb__JUN__ENCSR000EGH_1__m1     gene is annotated for similar motif hocomoco__...   
      dbcorrdb__BCL3__ENCSR000BQH_1__m2    gene is annotated for similar motif hocomoco__...   
      cisbp__M5050                         gene is annotated for similar motif hocomoco__...   

                                                                                              \
                                                                                     Context   
TF    MotifID                                                                                  
Arnt2 swissregulon__hs__AHR_ARNT_ARNT2.p2  (activating, weight>75.0%, mm9-tss-centered-10...   
Atf3  transfac_pro__M08931                 (activating, weight>75.0%, mm9-tss-centered-10...   
      dbcorrdb__JUN__ENCSR000EGH_1__m1     (activating, weight>75.0%, mm9-tss-centered-10...   
      dbcorrdb__BCL3__ENCSR000BQH_1__m2    (activating, weight>75.0%, mm9-tss-centered-10...   
      cisbp__M5050                         (activating, weight>75.0%, mm9-tss-centered-10...   

                                                                                              \
                                                                                 TargetGenes   
TF    MotifID                                                                                  
Arnt2 swissregulon__hs__AHR_ARNT_ARNT2.p2  [(Rab3a, 2.6908293773482725), (Pdgfb, 1.464523...   
Atf3  transfac_pro__M08931                 [(Junb, 68.93536816762585), (Npas4, 1.68751496...   
      dbcorrdb__JUN__ENCSR000EGH_1__m1     [(Lmna, 21.856685317989108), (Itpkc, 31.782767...   
      dbcorrdb__BCL3__ENCSR000BQH_1__m2    [(Kdm6b, 18.71394761738233), (Flnc, 1.05053630...   
      cisbp__M5050                         [(Npas4, 1.6875149686927675), (Ppl, 3.46665949...   

                                                     
                                          RankAtMax  
TF    MotifID                           

Display the enriched motifs with their associated sequence logos.

In [16]:
display_logos(df_motifs.head())

/home/ggj/anaconda3/envs/pyscenic/lib/python3.6/site-packages/ipykernel_launcher.py:20: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.


### STEP 4: Cellular enrichment aka AUCell

__REGULON CREATION__

Regulons can easily be created from this list of enriched motifs via `pyscenic.transform.df2regulons`. Here we provide an auxilliary function to carefully select the enriched motifs that contribute to the regulons.

In [20]:
def derive_regulons(motifs, db_names=('mm9-tss-centered-5kb-10species','mm9-tss-centered-10kb-7species','mm9-500bp-upstream-7species')):
    motifs.columns = motifs.columns.droplevel(0)

    def contains(*elems):
        def f(context):
            return any(elem in context for elem in elems)
        return f

    # For the creation of regulons we only keep the 10-species databases and the activating modules. We also remove the
    # enriched motifs for the modules that were created using the method 'weight>50.0%' (because these modules are not part
    # of the default settings of modules_from_adjacencies anymore.
    motifs = motifs[
        np.fromiter(map(compose(op.not_, contains('weight>50.0%')), motifs.Context), dtype=np.bool) & \
       # np.fromiter(map(contains(*db_names), motifs.Context), dtype=np.bool) & \
        np.fromiter(map(contains('activating'), motifs.Context), dtype=np.bool)]

    # We build regulons only using enriched motifs with a NES of 1.0 or higher; 
    #we take only directly annotated TFs or TF annotated
    # for an orthologous gene into account; and we only keep regulons with at least 1 genes.
    regulons = list(filter(lambda r: len(r) >= 1, df2regulons(motifs[(motifs['NES'] >= 1.0) 
                                                                      & ((motifs['Annotation'] == 'gene is directly annotated')
                                                                        | (motifs['Annotation'].str.startswith('gene is orthologous to')
                                                                           & motifs['Annotation'].str.endswith('which is directly annotated for motif')))
                                                                     ])))
    
    # Rename regulons, i.e. remove suffix.
    return list(map(lambda r: r.rename(r.transcription_factor), regulons))

In [21]:
regulons = derive_regulons(df_motifs)

Create regulons from a dataframe of enriched features.
Additional columns saved: []


In [17]:
import pyscenic

In [18]:
regulons=pyscenic.transform.df2regulons(df_motifs)

Create regulons from a dataframe of enriched features.
Additional columns saved: []


In [19]:
# Pickle these regulons.
with open(REGULONS_DAT_FNAME, 'wb') as f:
    pickle.dump(regulons, f)

In [20]:
len(regulons)

417

In [35]:
# Pickle these regulons.
with open(REGULONS_DAT_FNAME, 'wb') as f:
    pickle.dump(regulons, f)

__AUCELL__

In [ ]:
%%time
auc_mtx = aucell(df_tpm.T, regulons, num_workers=4)
auc_mtx.to_csv(AUCELL_MTX_FNAME)

```
CPU times: user 23.1 s, sys: 10.7 s, total: 33.8 s
Wall time: 39.2 s
```

In [13]:
auc_mtx

2410141K09Rik(+)  AW146154(+)    Ahr(+)  \
Cell                                                                           
Brain_2.TCGTAAGGGTTTAGTCGT_1                      0.0     0.000000  0.000000   
Brain_2.AAGCGGGTCCCGCGCACC_1                      0.0     0.000000  0.047847   
Brain_2.AGCGAGAGTCGTAGTCGT_1                      0.0     0.057665  0.051223   
Brain_2.CGAGTAACACCCGGCTGC_1                      0.0     0.000000  0.069735   
Brain_2.TTAACTCATCCCGAGATC_1                      0.0     0.070071  0.000000   
...                                               ...          ...       ...   
TwoYearsUterus_2.CTCGCAATGCTTCTCGCA               0.0     0.000000  0.000000   
TwoYearsUterus_3.CGAGTATGGATGTGCAAT               0.0     0.000000  0.000000   
TwoYearsUterus_2.CCAGACACGAGCCGCTTG               0.0     0.000000  0.000000   
TwoYearsUterus_5.AAGCGGCCTTTCGAGGAG               0.0     0.000000  0.000000   
TwoYearsUterus_3.ACTTATTATTGTTGCAAT               0.0     0.000000  0.040549   

                                      Alx1(+)     Ar(+)  Arid3a(+)   Arnt(+)  \
Cell                                                                           
Brain_2.TCGTAAGGGTTTAGTCGT_1         0.159394  0.041650   0.000000  0.049109   
Brain_2.AAGCGGGTCCCGCGCACC_1         0.000000  0.000017   0.004431  0.015931   
Brain_2.AGCGAGAGTCGTAGTCGT_1         0.000000  0.000110   0.002319  0.042343   
Brain_2.CGAGTAACACCCGGCTGC_1         0.000000  0.000224   0.007190  0.000796   
Brain_2.TTAACTCATCCCGAGATC_1         0.000000  0.000166   0.008534  0.040704   
...                                       ...       ...        ...       ...   
TwoYearsUterus_2.CTCGCAATGCTTCTCGCA  0.000000  0.065845   0.021784  0.076095   
TwoYearsUterus_3.CGAGTATGGATGTGCAAT  0.000000  0.000312   0.000000  0.063355   
TwoYearsUterus_2.CCAGACACGAGCCGCTTG  0.000000  0.066416   0.000000  0.079747   
TwoYearsUterus_5.AAGCGGCCTTTCGAGGAG  0.000000  0.089486   0.000000  0.091339   
TwoYearsUterus_3.ACTTATTATTGTTGCAAT  0.000000  0.056314   0.000000  0.109269   

                                     Arnt2(+)  Arx(+)  Ascl2(+)  ...  \
Cell                                                             ...   
Brain_2.TCGTAAGGGTTTAGTCGT_1         0.058756     0.0       0.0  ...   
Brain_2.AAGCGGGTCCCGCGCACC_1         0.077002     0.0       0.0  ...   
Brain_2.AGCGAGAGTCGTAGTCGT_1         0.065714     0.0       0.0  ...   
Brain_2.CGAGTAACACCCGGCTGC_1         0.048797     0.0       0.0  ...   
Brain_2.TTAACTCATCCCGAGATC_1         0.060181     0.0       0.0  ...   
...                                       ...     ...       ...  ...   
TwoYearsUterus_2.CTCGCAATGCTTCTCGCA  0.019565     0.0       0.0  ...   
TwoYearsUterus_3.CGAGTATGGATGTGCAAT  0.017453     0.0       0.0  ...   
TwoYearsUterus_2.CCAGACACGAGCCGCTTG  0.020260     0.0       0.0  ...   
TwoYearsUterus_5.AAGCGGCCTTTCGAGGAG  0.016391     0.0       0.0  ...   
TwoYearsUterus_3.ACTTATTATTGTTGCAAT  0.017929     0.0       0.0  ...   

                                     Zfp639(+)  Zfp64(+)  Zfp652(+)  \
Cell                                                                  
Brain_2.TCGTAAGGGTTTAGTCGT_1               0.0  0.000000   0.000000   
Brain_2.AAGCGGGTCCCGCGCACC_1               0.0  0.000000   0.154610   
Brain_2.AGCGAGAGTCGTAGTCGT_1               0.0  0.000000   0.000000   
Brain_2.CGAGTAACACCCGGCTGC_1               0.0  0.000000   0.000000   
Brain_2.TTAACTCATCCCGAGATC_1               0.0  0.000000   0.000000   
...                                        ...       ...        ...   
TwoYearsUterus_2.CTCGCAATGCTTCTCGCA        0.0  0.204672   0.078774   
TwoYearsUterus_3.CGAGTATGGATGTGCAAT        0.0  0.000000   0.000000   
TwoYearsUterus_2.CCAGACACGAGCCGCTTG        0.0  0.000000   0.084708   
TwoYearsUterus_5.AAGCGGCCTTTCGAGGAG        0.0  0.000000   0.000000   
TwoYearsUterus_3.ACTTATTATTGTTGCAAT        0.0  0.000000   0.000000   

                                     Zfp672(+)  Zfp740(+)  Zfp91(+)  \
Cell                   